In [31]:
# -*- coding: utf-8 -*-
import dataiku
import pandas as pd, numpy as np
from dataiku import pandasutils as pdu
from itertools import product
from gensim.models import word2vec
import itertools
from tqdm import tqdm 

In [24]:
# Read recipe inputs
reviews_TF_IDF = dataiku.Dataset("reviews_TF_IDF")
df = reviews_TF_IDF.get_dataframe()

In [25]:
folder_path = dataiku.Folder("m9JZdV7b").get_path()
model_path = folder_path + "/word2vec_ramen_model.model"
ramen_model = word2vec.Word2Vec.load(model_path)

In [26]:
store_cross = []
for ids in product(df['id'], repeat=2):
    store_cross.append(ids)

In [27]:
store_cross_df = pd.DataFrame(store_cross, columns=['id_x', 'id_y'])

In [28]:
store_cross_detail = store_cross_df.merge(df[['id','store_name','score','review_cnt','texts_tfidf_sorted_top20']], 
                                          how='inner', 
                                          left_on='id_x', 
                                          right_on='id').drop(columns='id').merge(df[['id','store_name','score','review_cnt','texts_tfidf_sorted_top20']], 
                                                                                  how='inner', 
                                                                                  left_on='id_y', 
                                                                                  right_on='id').drop(columns='id')

In [29]:
store_cross_detail.head()

id_x       id_y       store_name_x  score_x  review_cnt_x                         texts_tfidf_sorted_top20_x   store_name_y  score_y  review_cnt_y                         texts_tfidf_sorted_top20_y
0  ID-000001  ID-000001      手打式超多加水麺 ののくら     3.98           479  ['ワンタン', 'ストーブ', '予約', '2時間', '1時間', '記帳', '2時...  手打式超多加水麺 ののくら     3.98           479  ['ワンタン', 'ストーブ', '予約', '2時間', '1時間', '記帳', '2時...
1  ID-000002  ID-000001  Homemade Ramen 麦苗     3.97           731  ['記帳', 'ボード', 'ウェイティング', '深谷', '9時', '記名', 'ワン...  手打式超多加水麺 ののくら     3.98           479  ['ワンタン', 'ストーブ', '予約', '2時間', '1時間', '記帳', '2時...
2  ID-000003  ID-000001            麺尊 RAGE     3.96           723  ['金華', 'ハム', 'ロック', '穂先', '燻製', 'レモン', '豚バラ', ...  手打式超多加水麺 ののくら     3.98           479  ['ワンタン', 'ストーブ', '予約', '2時間', '1時間', '記帳', '2時...
3  ID-000004  ID-000001      宍道湖しじみ中華蕎麦 琥珀     3.95           296  ['シジミ', 'バラ', '焼き', '紫玉ねぎ', '吊し', '菅野', 'ワンタン'...  手打式超多加水麺 ののくら     3.98           479  ['ワンタン', 'ストーブ', '予約', '2時間', '1時間', '記帳', '2時...
4  ID-000005  ID-000001             らぁ麺や 嶋     3.95           177  ['記帳', '4点', '細切り', '記入', '炭火焼き', '昆布', '燻製', ...  手打式超多加水麺 ののくら     3.98           479  ['ワンタン', 'ストーブ', '予約', '2時間', '1時間', '記帳', '2時...

In [30]:
# store_cross_detail = store_cross_detail[store_cross_detail['id_x'].isin(df['id'].loc[0:50])]
store_cross_detail = store_cross_detail.reset_index(drop=True).sort_values(['id_x'])

In [32]:
##ラーメン店xに対してラーメン店yの類似度を算出
#コサイン類似度を算出する関数を定義
def cos_sim(v1, v2):
    return np.dot(v1, v2) / (np.linalg.norm(v1) * np.linalg.norm(v2))

In [0]:
#cossimだけの組み合わせ（同じワード同士の組みあわせがでてくるため）
#2次元を１次元にする　setが重複を削除てきなやつ。
# uniq_words = list(set(itertools.chain.from_iterable(df['texts_tfidf_sorted_top20'].values)))
word_list = []
arr = df['texts_tfidf_sorted_top20'].values
for a in arr:
    l = a.replace("'", "").replace("[", "").replace("]", "").replace(" ", "").split(",")
    word_list.append(l)
uniq_words = list(set(itertools.chain.from_iterable(word_list)))    
scores = {}
for word1, word2 in product(uniq_words, repeat=2):
    # print(word1, word2)
    scores[(word1, word2)] =  cos_sim(ramen_model.wv[word1], ramen_model.wv[word2])

豚脂 豚脂
豚脂 iphone
豚脂 厳禁
豚脂 31分
豚脂 建物
豚脂 狭い
豚脂 とうがらし
豚脂 うま
豚脂 41
豚脂 お湯
豚脂 ジェル
豚脂 つき
豚脂 ソースカツ丼
豚脂 団体
豚脂 おば
豚脂 ベーコン
豚脂 兄さん
豚脂 メタル
豚脂 凄まじい
豚脂 香辛料
豚脂 ボイル
豚脂 煮玉
豚脂 テープ
豚脂 白濁
豚脂 冷た
豚脂 ガリマヨ
豚脂 注ぎ口
豚脂 スプラウト
豚脂 鶏ガラ
豚脂 掛け
豚脂 焦げ
豚脂 小ぶり
豚脂 ーー
豚脂 木製
豚脂 貝出
豚脂 三河屋
豚脂 土屋
豚脂 コート
豚脂 豚骨スープ
豚脂 ドトール
豚脂 スタンプカード
豚脂 オレンジ色
豚脂 事項
豚脂 薬膳
豚脂 佃煮
豚脂 豚バラ
豚脂 七輪
豚脂 全開
豚脂 親父
豚脂 配分
豚脂 蒲鉾
豚脂 出迎え
豚脂 付与
豚脂 ニボスープ
豚脂 上等
豚脂 焙煎
豚脂 タブレット
豚脂 21時
豚脂 物足りな
豚脂 塩っぱく
豚脂 お客
豚脂 快感
豚脂 鶏団子
豚脂 控え目
豚脂 肉味噌
豚脂 バイク
豚脂 集合
豚脂 ピカイチ
豚脂 ビニール
豚脂 霧島
豚脂 好感
豚脂 伊勢海老
豚脂 個性的
豚脂 アルデンテ
豚脂 お麩
豚脂 大蒜
豚脂 蕎麦屋
豚脂 岩のり
豚脂 鶏の胸肉
豚脂 幸い
豚脂 ワタ
豚脂 カップル
豚脂 白い
豚脂 ピンクペッパー
豚脂 コンビーフ
豚脂 ロールチャーシュー
豚脂 指南
豚脂 挨拶
豚脂 エグ
豚脂 カフェ
豚脂 豚肩ロース
豚脂 qrコード
豚脂 2階
豚脂 ウマイ
豚脂 黒っぽい
豚脂 セロリ
豚脂 スゲー
豚脂 アタマ
豚脂 ルール
豚脂 本節
豚脂 サイン
豚脂 口中
豚脂 シャバ
豚脂 フレーク
豚脂 細切れ
豚脂 苦み
豚脂 グラス
豚脂 辛味
豚脂 ヤミツキ
豚脂 サッパリ
豚脂 モヤシ
豚脂 広い
豚脂 ガニ
豚脂 天邪鬼
豚脂 最終的
豚脂 にくい
豚脂 西山
豚脂 ゼリー
豚脂 電話
豚脂 ドロ
豚脂 お通し
豚脂 ウェーブ
豚脂 薄暗く
豚脂 胡椒
豚脂 煮豚
豚脂 フレッシュ
豚脂 七福
豚脂 金華
豚脂 シャキ
豚脂 お餅
豚脂 エッジ
豚脂 旨かっ
豚脂 抽出
豚脂 イタリア産
豚脂 物腰
豚脂 陽気
豚脂 薄切り
豚脂 カーブ
豚脂 小料理
豚脂 太平
豚脂 エスプーマ
豚脂 酒井
豚脂 烏龍茶


iphone 苦み
iphone グラス
iphone 辛味
iphone ヤミツキ
iphone サッパリ
iphone モヤシ
iphone 広い
iphone ガニ
iphone 天邪鬼
iphone 最終的
iphone にくい
iphone 西山
iphone ゼリー
iphone 電話
iphone ドロ
iphone お通し
iphone ウェーブ
iphone 薄暗く
iphone 胡椒
iphone 煮豚
iphone フレッシュ
iphone 七福
iphone 金華
iphone シャキ
iphone お餅
iphone エッジ
iphone 旨かっ
iphone 抽出
iphone イタリア産
iphone 物腰
iphone 陽気
iphone 薄切り
iphone カーブ
iphone 小料理
iphone 太平
iphone エスプーマ
iphone 酒井
iphone 烏龍茶
iphone air
iphone エシャロット
iphone 紫蘇
iphone 内臓
iphone 鮮明
iphone 派手
iphone パウダー
iphone エビ
iphone 濃いめ
iphone 割り
iphone 衝立
iphone 防止
iphone 丸く
iphone シンプル
iphone 両立
iphone 生地
iphone 粉末
iphone めんま
iphone 切れ端
iphone 外人
iphone 端麗
iphone アラ
iphone 想定内
iphone 紅白
iphone ロッド
iphone へん
iphone 包丁
iphone 向き
iphone ゲット
iphone 能書き
iphone 十二分
iphone スタイル
iphone 固い
iphone タラ
iphone 猪又
iphone 梅干し
iphone 左右
iphone ペッパー
iphone 薫香
iphone 臭み
iphone 西山製麺
iphone 拍子抜け
iphone 硬い
iphone 塩辛かっ
iphone 38
iphone すり身
iphone 小声
iphone 緻密
iphone トゥルン
iphone ドレッシング
iphone 熱心
iphone 水平
iphone 塩っぱい
iphone 青唐辛子
iphone 気配り


iphone お米
iphone ツル
iphone ニンニク
iphone 魚の
iphone 半券
iphone 玉ネギ
iphone 平太
iphone 可愛く
iphone 女性
iphone ドボン
iphone サバ
iphone ローテーション
iphone おしゃれ
iphone 作り
iphone 低温
iphone リーフ
iphone 油膜
iphone 3種
iphone 西京
iphone お肉
iphone 柑橘系
iphone コッテリ
iphone 採用
iphone 縮れ麺
iphone クラゲ
iphone メリハリ
iphone 長ネギ
iphone 柚子胡椒
iphone アサリ
iphone 塩加減
iphone 石臼挽き
iphone とも
iphone 三分
iphone 華やかさ
iphone ムッチリ
iphone 黄色
iphone マッシュルーム
iphone ol
iphone やわらかく
iphone ありか
iphone でかい
iphone 重厚
iphone イクラ
iphone 野菜
iphone ブラックペッパー
iphone ガラス
iphone フライドガーリック
iphone ゆず
iphone パプリカ
iphone 黒ラベル
iphone 背番号
iphone ヘルシー
iphone 動揺
iphone 1時間前
iphone 手渡し
iphone 繁盛店
iphone 赤褐色
iphone タマリンド
iphone 香味
iphone 応え
iphone ハイブリッド
iphone コース料理
iphone 受付
iphone 鉄板
iphone 明る
iphone シート
iphone パフォーマンス
iphone 炭水化物
iphone 大山どり
iphone 3割
iphone ほうとう
iphone 再来
iphone 14
iphone レモン
iphone 九条葱
iphone コロナ対応
iphone 待合
iphone ローストポーク
iphone 調理方法
iphone 名簿
iphone ハード
iphone 無化調
iphone なめこ
iphone シャクシャク
iphone 悪天候
iphone グッズ
iphone デロデロ
iphone 甘辛い
iphone

厳禁 マイルド
厳禁 格闘
厳禁 タケノコ
厳禁 キッチン
厳禁 rdb
厳禁 モニター
厳禁 探索
厳禁 隔離
厳禁 待ち人
厳禁 細長
厳禁 レストラン
厳禁 20
厳禁 トロ
厳禁 おかしく
厳禁 乳白色
厳禁 青ねぎ
厳禁 喧騒
厳禁 腹ペコ
厳禁 がい
厳禁 つる
厳禁 オーション
厳禁 しゃぶしゃぶ
厳禁 カラメ
厳禁 豚骨
厳禁 一つ一つ
厳禁 撮影
厳禁 裏口
厳禁 半熟卵
厳禁 ズシリ
厳禁 ほうれん草
厳禁 オン
厳禁 岩中
厳禁 ニボニボ
厳禁 オーブン
厳禁 山水
厳禁 クシ
厳禁 隙間
厳禁 エスニック
厳禁 モミジ
厳禁 カイワレ大根
厳禁 ワンポイント
厳禁 葛西
厳禁 部分
厳禁 硬く
厳禁 危ない
厳禁 レア
厳禁 だし
厳禁 不規則
厳禁 ぷり
厳禁 クラシカル
厳禁 14分
厳禁 クミン
厳禁 小海老
厳禁 大鍋
厳禁 つるし
厳禁 苦味
厳禁 コレ
厳禁 ワシワシ
厳禁 ソープ
厳禁 液体
厳禁 暗く
厳禁 背後
厳禁 角切
厳禁 リフトアップ
厳禁 輪切り
厳禁 ランチョンマット
厳禁 2時間半
厳禁 北海道
厳禁 整理券
厳禁 長方形
厳禁 間引き
厳禁 濃密
厳禁 記入
厳禁 出して
厳禁 北海道産
厳禁 みょうが
厳禁 トンコツ
厳禁 切れ味
厳禁 美人
厳禁 対極
厳禁 厳選
厳禁 柚子
厳禁 ズズズ
厳禁 オブジェ
厳禁 煮込み
厳禁 どろどろ
厳禁 柚子の皮
厳禁 内観
厳禁 作戦
厳禁 10人
厳禁 女子
厳禁 ミスマッチ
厳禁 真っ白
厳禁 クタ
厳禁 バーナー
厳禁 肉汁
厳禁 すき
厳禁 貝割れ
厳禁 居抜き
厳禁 メール
厳禁 にこやか
厳禁 コーヒーサイフォン
厳禁 ゆで卵
厳禁 ワイルド
厳禁 スイカ
厳禁 生臭
厳禁 仕様
厳禁 配慮
厳禁 そうめん
厳禁 お札
厳禁 お洒落
厳禁 干し海老
厳禁 片口鰯
厳禁 キクラゲ
厳禁 プリッ
厳禁 丸大
厳禁 当日
厳禁 組み合わせ
厳禁 要請
厳禁 浅草開化楼
厳禁 深く
厳禁 ナチュラル
厳禁 スモーク
厳禁 たまねぎ
厳禁 ペースト状
厳禁 ウルメイワシ
厳禁 丸太
厳禁 煮汁
厳禁 人前
厳禁 オイリー
厳禁 9番
厳禁 挽き肉
厳禁 パツッ
厳禁 づる
厳禁 叉焼
厳禁 単体
厳禁 塩辛い
厳禁 スピーディー
厳禁 間際
厳禁 狭かっ
厳禁 ぼ

31分 豚骨スープ
31分 ドトール
31分 スタンプカード
31分 オレンジ色
31分 事項
31分 薬膳
31分 佃煮
31分 豚バラ
31分 七輪
31分 全開
31分 親父
31分 配分
31分 蒲鉾
31分 出迎え
31分 付与
31分 ニボスープ
31分 上等
31分 焙煎
31分 タブレット
31分 21時
31分 物足りな
31分 塩っぱく
31分 お客
31分 快感
31分 鶏団子
31分 控え目
31分 肉味噌
31分 バイク
31分 集合
31分 ピカイチ
31分 ビニール
31分 霧島
31分 好感
31分 伊勢海老
31分 個性的
31分 アルデンテ
31分 お麩
31分 大蒜
31分 蕎麦屋
31分 岩のり
31分 鶏の胸肉
31分 幸い
31分 ワタ
31分 カップル
31分 白い
31分 ピンクペッパー
31分 コンビーフ
31分 ロールチャーシュー
31分 指南
31分 挨拶
31分 エグ
31分 カフェ
31分 豚肩ロース
31分 qrコード
31分 2階
31分 ウマイ
31分 黒っぽい
31分 セロリ
31分 スゲー
31分 アタマ
31分 ルール
31分 本節
31分 サイン
31分 口中
31分 シャバ
31分 フレーク
31分 細切れ
31分 苦み
31分 グラス
31分 辛味
31分 ヤミツキ
31分 サッパリ
31分 モヤシ
31分 広い
31分 ガニ
31分 天邪鬼
31分 最終的
31分 にくい
31分 西山
31分 ゼリー
31分 電話
31分 ドロ
31分 お通し
31分 ウェーブ
31分 薄暗く
31分 胡椒
31分 煮豚
31分 フレッシュ
31分 七福
31分 金華
31分 シャキ
31分 お餅
31分 エッジ
31分 旨かっ
31分 抽出
31分 イタリア産
31分 物腰
31分 陽気
31分 薄切り
31分 カーブ
31分 小料理
31分 太平
31分 エスプーマ
31分 酒井
31分 烏龍茶
31分 air
31分 エシャロット
31分 紫蘇
31分 内臓
31分 鮮明
31分 派手
31分 パウダー
31分 エビ
31分 濃いめ
31分 割り
31分 衝立
31分 防止
31分 丸く
31分 シンプル
31分 両立
31分 生地
31分 粉末
31分 めんま
31分 切れ端
31分 外人
31分

...

処理 重たい
処理 今一つ
処理 豪快
処理 ロース
処理 モモ
処理 湯切り
処理 胚芽
処理 滋味
処理 小さく
処理 ビニールシート
処理 ポタージュ
処理 サワークリーム
処理 静か
処理 蘊蓄
処理 カオス
処理 とろみ
処理 4人
処理 新鮮
処理 おしぼり
処理 お醤油
処理 17分
処理 女性客
処理 ざく
処理 素早い
処理 ちゃんぽん
処理 鶏手羽先
処理 間接照明
処理 お盆
処理 本館
処理 オニオン
処理 甲殻類
処理 歯切れ
処理 漆黒
処理 天下一品
処理 来店客
処理 軽快
処理 揚げ
処理 ポルチーニデュクセル
処理 全面
処理 ゲスト
処理 乳化
処理 束の間
処理 かたく
処理 ポリ
処理 反射
処理 及第点
処理 ワンタン
処理 オシャレ
処理 万能ネギ
処理 駐輪場
処理 細切り
処理 鶏ムネ肉
処理 ヒバジ
処理 交代
処理 1本
処理 熟成
処理 脇役
処理 七味
処理 20時
処理 推測
処理 ソース
処理 覆面
処理 鶏がら
処理 ボトル
処理 スーフ
処理 辛み
処理 フォルム
処理 たけのこ
処理 ジュレ
処理 さりげ
処理 まぜまぜ
処理 1時間
処理 ミンチ
処理 ブロック
処理 インカベリーソース
処理 アワビ
処理 親子
処理 食べ方
処理 素朴
処理 筆者
処理 病みつき
処理 茨城県
処理 カラスミ
処理 ゴマ
処理 三密
処理 シャモ
処理 万能ねぎ
処理 あん肝
処理 濃ゆい
処理 ぷりっぷり
処理 花びら
処理 with
処理 肉団子
処理 微塵
処理 製麺機
処理 動き
処理 スダチ
処理 部屋
処理 にく
処理 定義
処理 サラリーマン
処理 25人
処理 下支え
処理 変化
処理 爪楊枝
処理 カタ
処理 宗田
処理 お口
処理 ナッツ
処理 柚子皮
処理 チープ
処理 真逆
処理 堅め
処理 グレープフルーツ
処理 文句なし
処理 おしゃべり
処理 三角形
処理 担当
処理 テキ
処理 一味唐辛子
処理 豚肩ロース肉
処理 4種
処理 白ねぎ
処理 ミツバ
処理 かいわれ大根
処理 照明
処理 しや
処理 トロッ
処理 青海苔
処理 13分
処理 手洗い
処理 砂糖
処理 16分
処理 天井
処理 密か
処理 コショウ
処理 鶏挽肉
処理 白味噌
処理 4点
処理 階段
処理 蒸し鶏
処

三つ葉 店構え
三つ葉 吸収
三つ葉 脂っこい
三つ葉 もち
三つ葉 由来
三つ葉 だれ
三つ葉 うま味
三つ葉 テキパキ
三つ葉 カネ
三つ葉 出来
三つ葉 呼び出し
三つ葉 女将
三つ葉 作り置き
三つ葉 ファミレス
三つ葉 ツルツルシコシコ
三つ葉 短い
三つ葉 薫製
三つ葉 程よく
三つ葉 穏やか
三つ葉 平打
三つ葉 パスタ
三つ葉 発券
三つ葉 シナチク
三つ葉 へーき
三つ葉 主人
三つ葉 冷たく
三つ葉 メチャクチャ
三つ葉 飲食
三つ葉 会津地鶏
三つ葉 忠実
三つ葉 おっさん
三つ葉 真っ黒
三つ葉 特殊
三つ葉 申し訳
三つ葉 家元
三つ葉 滑り
三つ葉 アジア系
三つ葉 質感
三つ葉 穂先
三つ葉 記名
三つ葉 充満
三つ葉 軟骨
三つ葉 路上
三つ葉 基調
三つ葉 中太
三つ葉 コハク酸
三つ葉 発行
三つ葉 生醤油
三つ葉 魚醤
三つ葉 3日間
三つ葉 広がり
三つ葉 辣油
三つ葉 かも
三つ葉 方向性
三つ葉 開花
三つ葉 新芽
三つ葉 八角
三つ葉 分厚く
三つ葉 貝柱
三つ葉 岩海苔
三つ葉 サラ
三つ葉 白胡麻
三つ葉 煮卵
三つ葉 ブロス
三つ葉 ハワイ
三つ葉 2本
三つ葉 仄か
三つ葉 ゚と
三つ葉 存分
三つ葉 外側
三つ葉 白め
三つ葉 サイン色紙
三つ葉 ハム
三つ葉 レアチャー
三つ葉 ダシ
三つ葉 アーリーレッド
三つ葉 玄米
三つ葉 紅ショウガ
三つ葉 栄養
三つ葉 注意書き
三つ葉 既存
三つ葉 刻みニンニク
三つ葉 27分
三つ葉 淡い
三つ葉 ひとり
三つ葉 細い
三つ葉 ドゥエ
三つ葉 25分
三つ葉 ハンド
三つ葉 ひと
三つ葉 イキイキ
三つ葉 トマトソース
三つ葉 宮崎県
三つ葉 玉葱
三つ葉 ポット
三つ葉 シロップ
三つ葉 真昆布
三つ葉 6枚
三つ葉 鮮度
三つ葉 パンパン
三つ葉 瞬間
三つ葉 入れ替え
三つ葉 ベビーリーフ
三つ葉 カツオ
三つ葉 会津
三つ葉 ピーナッツ
三つ葉 line
三つ葉 小さ
三つ葉 最後列
三つ葉 レタス
三つ葉 でっかい
三つ葉 アジ
三つ葉 ニンジン
三つ葉 洋風
三つ葉 触り
三つ葉 初め
三つ葉 設計
三つ葉 トレー
三つ葉 煮干し
三つ葉 上手い
三つ葉 トイレ
三つ葉 明るい
三つ葉 ホロリ
三つ葉 混濁
三つ葉 嶋崎
三つ葉 味つけ
三つ葉 柔ら

佇まい ドン
佇まい 名分
佇まい カタメ
佇まい ニラ
佇まい シャッター
佇まい ロースト
佇まい 椅子
佇まい 太め
佇まい パイ
佇まい わかめ
佇まい 白髪ねぎ
佇まい うめぇ
佇まい 搾菜
佇まい 熱々
佇まい 塩辛く
佇まい 緑色
佇まい ガリシア
佇まい バター
佇まい 枯節
佇まい 的確
佇まい ザク
佇まい 灰汁
佇まい 回収
佇まい 平たい
佇まい 何れ
佇まい 前後
佇まい バラ肉
佇まい ハラ
佇まい 配布
佇まい ローストビーフ
佇まい 善き
佇まい お母さん
佇まい サポート
佇まい 予約
佇まい 花鰹
佇まい 天草大王
佇まい 干し椎茸
佇まい カルテット
佇まい フライドオニオン
佇まい 小さめ
佇まい 小野里
佇まい 冷え冷え
佇まい すだち
佇まい テンポ
佇まい 豊潤
佇まい 低め
佇まい 天候
佇まい 自家製
佇まい 扇風機
佇まい ランス
佇まい 山盛り
佇まい 感覚
佇まい ブラウン
佇まい 手際
佇まい サイコロ
佇まい 海産物
佇まい 9時
佇まい すり
佇まい レバー
佇まい イイ
佇まい 果汁
佇まい このまま
佇まい 頂戴
佇まい covid-19
佇まい プリン
佇まい 明確
佇まい パワー
佇まい 村上
佇まい 和風
佇まい キリン
佇まい 加速
佇まい たたき
佇まい 12分
佇まい パーティション
佇まい 罪悪感
佇まい カラメコール
佇まい ランダム
佇まい ガラガラ
佇まい 薄口醤油
佇まい づらい
佇まい チンゲン菜
佇まい ナルト
佇まい クワイ
佇まい ノドグロ
佇まい マゼマゼ
佇まい ラジオ
佇まい 鶏油
佇まい 賑やか
佇まい 湯気
佇まい 鶏もも
佇まい 12人
佇まい 切れ
佇まい お冷
佇まい お次
佇まい 長葱
佇まい 待ち客
佇まい 火入れ
佇まい ガテン系
佇まい 冷蔵庫
佇まい 7人
佇まい 重たく
佇まい 26分
佇まい jazz
佇まい カレー粉
佇まい 天地返し
佇まい 割合
佇まい ホウレンソウ
佇まい 造り
佇まい 木造
佇まい チャーシュ
佇まい ヤワ
佇まい パサ
佇まい 田村
佇まい ぶつ切り
佇まい 老夫婦
佇まい 鰹出汁
佇まい 複雑
佇まい 所要時間
佇まい 和食屋
佇まい クリガニ
佇まい 塩漬け
佇まい 改装
佇まい ブロッコリー
佇まい 焼肉
佇

貝汁 ガラ
貝汁 スナック
貝汁 セメント
貝汁 カク
貝汁 1120円
貝汁 柑橘
貝汁 ゴワ
貝汁 間近
貝汁 お茶
貝汁 比べ
貝汁 豆腐
貝汁 ウェイト
貝汁 テーブル席
貝汁 ホット
貝汁 ミソ
貝汁 クリーム
金髪 豚脂
金髪 iphone
金髪 厳禁
金髪 31分
金髪 建物
金髪 狭い
金髪 とうがらし
金髪 うま
金髪 41
金髪 お湯
金髪 ジェル
金髪 つき
金髪 ソースカツ丼
金髪 団体
金髪 おば
金髪 ベーコン
金髪 兄さん
金髪 メタル
金髪 凄まじい
金髪 香辛料
金髪 ボイル
金髪 煮玉
金髪 テープ
金髪 白濁
金髪 冷た
金髪 ガリマヨ
金髪 注ぎ口
金髪 スプラウト
金髪 鶏ガラ
金髪 掛け
金髪 焦げ
金髪 小ぶり
金髪 ーー
金髪 木製
金髪 貝出
金髪 三河屋
金髪 土屋
金髪 コート
金髪 豚骨スープ
金髪 ドトール
金髪 スタンプカード
金髪 オレンジ色
金髪 事項
金髪 薬膳
金髪 佃煮
金髪 豚バラ
金髪 七輪
金髪 全開
金髪 親父
金髪 配分
金髪 蒲鉾
金髪 出迎え
金髪 付与
金髪 ニボスープ
金髪 上等
金髪 焙煎
金髪 タブレット
金髪 21時
金髪 物足りな
金髪 塩っぱく
金髪 お客
金髪 快感
金髪 鶏団子
金髪 控え目
金髪 肉味噌
金髪 バイク
金髪 集合
金髪 ピカイチ
金髪 ビニール
金髪 霧島
金髪 好感
金髪 伊勢海老
金髪 個性的
金髪 アルデンテ
金髪 お麩
金髪 大蒜
金髪 蕎麦屋
金髪 岩のり
金髪 鶏の胸肉
金髪 幸い
金髪 ワタ
金髪 カップル
金髪 白い
金髪 ピンクペッパー
金髪 コンビーフ
金髪 ロールチャーシュー
金髪 指南
金髪 挨拶
金髪 エグ
金髪 カフェ
金髪 豚肩ロース
金髪 qrコード
金髪 2階
金髪 ウマイ
金髪 黒っぽい
金髪 セロリ
金髪 スゲー
金髪 アタマ
金髪 ルール
金髪 本節
金髪 サイン
金髪 口中
金髪 シャバ
金髪 フレーク
金髪 細切れ
金髪 苦み
金髪 グラス
金髪 辛味
金髪 ヤミツキ
金髪 サッパリ
金髪 モヤシ
金髪 広い
金髪 ガニ
金髪 天邪鬼
金髪 最終的
金髪 にくい
金髪 西山
金髪 ゼリー
金髪 電話
金髪 ドロ
金髪 お通し
金髪 ウェーブ
金髪 薄暗く
金髪 胡椒
金髪 煮豚
金髪 フレッシュ
金髪 七

卵黄 後藤
卵黄 美味しいー
卵黄 接客
卵黄 鶏もも肉
卵黄 細平
卵黄 玉ねぎ
卵黄 金原
卵黄 東南アジア
卵黄 黒烏龍茶
卵黄 香味油
卵黄 青菜
卵黄 黒酢
卵黄 大川
卵黄 小松菜
卵黄 変貌
卵黄 メンマ
卵黄 高水準
卵黄 ぴろ
卵黄 海塩
卵黄 当方
卵黄 モチ
卵黄 団子
卵黄 色紙
卵黄 私達
卵黄 客席
卵黄 塩分濃度
卵黄 花山椒
卵黄 記帳
卵黄 待人
卵黄 づつ
卵黄 タレ
卵黄 ゼラチン
卵黄 がけ
卵黄 スポンジ
卵黄 元気
卵黄 一蘭
卵黄 酸っぱい
卵黄 トロミ
卵黄 番号
卵黄 1cm
卵黄 クレソン
卵黄 山上
卵黄 まーす
卵黄 淡麗
卵黄 黒胡椒
卵黄 15人
卵黄 ディスプレイ
卵黄 グラマス
卵黄 お客さま
卵黄 海苔
卵黄 シッカリ
卵黄 キャビア
卵黄 れんげ
卵黄 いいね
卵黄 処理
卵黄 三つ葉
卵黄 佇まい
卵黄 貝汁
卵黄 金髪
卵黄 卵黄
卵黄 50分
卵黄 不在
卵黄 祖師谷
卵黄 呪文
卵黄 おろしニンニク
卵黄 寒い
卵黄 奥様
卵黄 清掃
卵黄 いしる
卵黄 6番手
卵黄 オリーブオイル
卵黄 瀬戸内海
卵黄 かいわれ
卵黄 厚く
卵黄 ボリューム
卵黄 うるめ
卵黄 秘伝
卵黄 なめらか
卵黄 チップ
卵黄 平打ち
卵黄 ヤングコーン
卵黄 鰹節
卵黄 勝ち
卵黄 ぃぃ
卵黄 昔ながらの
卵黄 合盛り
卵黄 甘く
卵黄 洋梨
卵黄 だそう
卵黄 香味野菜
卵黄 痺れ
卵黄 かな
卵黄 平べったい
卵黄 恐縮
卵黄 青ネギ
卵黄 返却
卵黄 アスパラガス
卵黄 一軒家
卵黄 方々
卵黄 ヤツ
卵黄 ジャズ
卵黄 春菊
卵黄 上述
卵黄 アタック
卵黄 ランチメニュー
卵黄 両サイド
卵黄 視線
卵黄 序盤
卵黄 ぉぉ
卵黄 活気
卵黄 クド
卵黄 緩やか
卵黄 オクラ
卵黄 ゾーン
卵黄 好感度
卵黄 ソフト
卵黄 焼き
卵黄 キノコ
卵黄 麦芽
卵黄 導入
卵黄 山芋
卵黄 マイルド
卵黄 格闘
卵黄 タケノコ
卵黄 キッチン
卵黄 rdb
卵黄 モニター
卵黄 探索
卵黄 隔離
卵黄 待ち人
卵黄 細長
卵黄 レストラン
卵黄 20
卵黄 トロ
卵黄 おかしく
卵黄 乳白色
卵黄 青ねぎ
卵黄 喧騒
卵黄 腹ペコ
卵黄 がい
卵黄 つる
卵黄 オーション
卵黄 しゃぶしゃぶ
卵黄 カラメ
卵

In [50]:
df['texts_tfidf_sorted_top20'].values[0].replace("'", "").replace("[", "").replace("]", "").replace(" ", "").split(",")

AttributeError: 'numpy.ndarray' object has no attribute 'replace'

In [52]:
word_list = []
arr = df['texts_tfidf_sorted_top20'].values
for a in arr:
    l = a.replace("'", "").replace("[", "").replace("]", "").replace(" ", "").split(",")
    word_list.append(l)

In [56]:
list(set(itertools.chain.from_iterable(word_list)))

['豚脂',
 'iphone',
 '厳禁',
 '31分',
 '建物',
 '狭い',
 'とうがらし',
 'うま',
 '41',
 'お湯',
 'ジェル',
 'つき',
 'ソースカツ丼',
 '団体',
 'おば',
 'ベーコン',
 '兄さん',
 'メタル',
 '凄まじい',
 '香辛料',
 'ボイル',
 '煮玉',
 'テープ',
 '白濁',
 '冷た',
 'ガリマヨ',
 '注ぎ口',
 'スプラウト',
 '鶏ガラ',
 '掛け',
 '焦げ',
 '小ぶり',
 'ーー',
 '木製',
 '貝出',
 '三河屋',
 '土屋',
 'コート',
 '豚骨スープ',
 'ドトール',
 'スタンプカード',
 'オレンジ色',
 '事項',
 '薬膳',
 '佃煮',
 '豚バラ',
 '七輪',
 '全開',
 '親父',
 '配分',
 '蒲鉾',
 '出迎え',
 '付与',
 'ニボスープ',
 '上等',
 '焙煎',
 'タブレット',
 '21時',
 '物足りな',
 '塩っぱく',
 'お客',
 '快感',
 '鶏団子',
 '控え目',
 '肉味噌',
 'バイク',
 '集合',
 'ピカイチ',
 'ビニール',
 '霧島',
 '好感',
 '伊勢海老',
 '個性的',
 'アルデンテ',
 'お麩',
 '大蒜',
 '蕎麦屋',
 '岩のり',
 '鶏の胸肉',
 '幸い',
 'ワタ',
 'カップル',
 '白い',
 'ピンクペッパー',
 'コンビーフ',
 'ロールチャーシュー',
 '指南',
 '挨拶',
 'エグ',
 'カフェ',
 '豚肩ロース',
 'qrコード',
 '2階',
 'ウマイ',
 '黒っぽい',
 'セロリ',
 'スゲー',
 'アタマ',
 'ルール',
 '本節',
 'サイン',
 '口中',
 'シャバ',
 'フレーク',
 '細切れ',
 '苦み',
 'グラス',
 '辛味',
 'ヤミツキ',
 'サッパリ',
 'モヤシ',
 '広い',
 'ガニ',
 '天邪鬼',
 '最終的',
 'にくい',
 '西山',
 'ゼリー',
 '電話',
 'ドロ',
 'お通し',
 'ウェーブ',
 '薄暗く',
 '胡椒',
 '煮豚',

In [16]:
avg_avg_scores = []
for i in tqdm(range(len(store_cross_detail['texts_tfidf_sorted_top20_x']))):
    avg_scores = []
    for j in range(len(store_cross_detail['texts_tfidf_sorted_top20_x'][i])):
        word_cross_scores = []
        word_a = store_cross_detail['texts_tfidf_sorted_top20_x'][i][j]
        for k in range(len(store_cross_detail['texts_tfidf_sorted_top20_y'][i])):
            word_b = store_cross_detail['texts_tfidf_sorted_top20_y'][i][k]
            score = scores[(word_a, word_b)]#単語間のスコアを出す。
            word_cross_scores.append(score)
        avg_scores.append(np.mean(word_cross_scores))#20個の単語間スコアの平均値
    avg_avg_scores.append(np.mean(avg_scores))#20個の単語間スコアの平均値の平均値
store_cross_detail.insert(6, 'avg_cos_sim_rate', avg_avg_scores)  
# 「二郎」と類似度が高いラーメン屋を高い順に表示
store_cross_detail = store_cross_detail.sort_values(['id_x', 'avg_cos_sim_rate'], ascending=[True, False])
df_sim_x = store_cross_detail[store_cross_detail['store_name_x'].str.contains('二郎')]
df_sim_x.reset_index(drop=True)

def min_max(x, axis=None):
    min = x.min(axis=axis, keepdims=True)
    max = x.max(axis=axis, keepdims=True)
    result = (x-min)/(max-min)
    return result
b = df_sim_x['avg_cos_sim_rate']
c = min_max(b.values)
df_sim_x.insert(7, '正規化', c)
df_sim_x

NameError: name 'store_df' is not defined

In [0]:
# Compute recipe outputs from inputs
# TODO: Replace this part by your actual code that computes the output, as a Pandas dataframe
# NB: DSS also supports other kinds of APIs for reading and writing data. Please see doc.

similarity_scores_df = reviews_TF_IDF_df # For this sample code, simply copy input to output


# Write recipe outputs
similarity_scores = dataiku.Dataset("similarity_scores")
similarity_scores.write_with_schema(similarity_scores_df)